In [1]:
import pandas as pd
import numpy as np

In [2]:
df=pd.read_csv('tips.csv')

In [3]:
df.replace('',np.nan,inplace=True) 

In [4]:
df.isnull().sum()

total_bill    0
tip           0
sex           0
smoker        0
day           0
time          0
size          0
dtype: int64

In [5]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 244 entries, 0 to 243
Data columns (total 7 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   total_bill  244 non-null    float64
 1   tip         244 non-null    float64
 2   sex         244 non-null    object 
 3   smoker      244 non-null    object 
 4   day         244 non-null    object 
 5   time        244 non-null    object 
 6   size        244 non-null    int64  
dtypes: float64(2), int64(1), object(4)
memory usage: 13.5+ KB


### Encodiing

In [6]:
df.sex.replace({'Female':0,'Male':1},inplace=True)
df.smoker.replace({'No':0,'Yes':1},inplace=True)
df.day.replace({'Thur':0,'Fri':1,'Sat':2,'Sun':3},inplace=True)
df.time.replace({'Lunch':0,'Dinner':1},inplace=True)

In [7]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 244 entries, 0 to 243
Data columns (total 7 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   total_bill  244 non-null    float64
 1   tip         244 non-null    float64
 2   sex         244 non-null    int64  
 3   smoker      244 non-null    int64  
 4   day         244 non-null    int64  
 5   time        244 non-null    int64  
 6   size        244 non-null    int64  
dtypes: float64(2), int64(5)
memory usage: 13.5 KB


In [8]:
df['tip_rate']=(df.tip/df.total_bill*100).round()

In [9]:
df.describe()

total_bill         tip         sex      smoker         day        time  \
count  244.000000  244.000000  244.000000  244.000000  244.000000  244.000000   
mean    19.785943    2.998279    0.643443    0.381148    1.725410    0.721311   
std      8.902412    1.383638    0.479967    0.486667    1.155774    0.449276   
min      3.070000    1.000000    0.000000    0.000000    0.000000    0.000000   
25%     13.347500    2.000000    0.000000    0.000000    0.000000    0.000000   
50%     17.795000    2.900000    1.000000    0.000000    2.000000    1.000000   
75%     24.127500    3.562500    1.000000    1.000000    3.000000    1.000000   
max     50.810000   10.000000    1.000000    1.000000    3.000000    1.000000   

             size    tip_rate  
count  244.000000  244.000000  
mean     2.569672   16.094262  
std      0.951100    6.102968  
min      1.000000    4.000000  
25%      2.000000   13.000000  
50%      2.000000   15.500000  
75%      3.000000   19.000000  
max      6.000000   71.000000

In [10]:
df.head()

total_bill   tip  sex  smoker  day  time  size  tip_rate
0       16.99  1.01    0       0    3     1     2       6.0
1       10.34  1.66    1       0    3     1     3      16.0
2       21.01  3.50    1       0    3     1     3      17.0
3       23.68  3.31    1       0    3     1     2      14.0
4       24.59  3.61    0       0    3     1     4      15.0

### RFE

In [11]:
y=df.tip

In [12]:
X=df.drop('tip',axis=1)

In [13]:
X

total_bill  sex  smoker  day  time  size  tip_rate
0         16.99    0       0    3     1     2       6.0
1         10.34    1       0    3     1     3      16.0
2         21.01    1       0    3     1     3      17.0
3         23.68    1       0    3     1     2      14.0
4         24.59    0       0    3     1     4      15.0
..          ...  ...     ...  ...   ...   ...       ...
239       29.03    1       0    2     1     3      20.0
240       27.18    0       1    2     1     2       7.0
241       22.67    1       1    2     1     2       9.0
242       17.82    1       0    2     1     2      10.0
243       18.78    0       0    0     1     2      16.0

[244 rows x 7 columns]

In [14]:
data=X.values

In [15]:
y=y.values

In [16]:
sum(np.isnan(data).flatten())

0

In [17]:
sum(np.isnan(y).flatten())

0

In [18]:
# 지금은 없지만 나중을 위해 기록
# imputer = SimpleImputer(strategy='median')

In [19]:
# imputer.fit(data)

In [20]:
# data_trans=imputer.transform(data)

In [21]:
from sklearn.feature_selection import RFE
from sklearn.svm import SVR

In [22]:
estimator=SVR(kernel='linear')

In [23]:
rfe = RFE(estimator, n_features_to_select=4)

In [24]:
data.shape

(244, 7)

In [25]:
rfe.fit(data,y)

RFE(estimator=SVR(kernel='linear'), n_features_to_select=4)

In [26]:
for i in range(data.shape[1]):
  print('Column: %10s, Rank: %d' % (X.columns[i], rfe.ranking_[i]))

Column: total_bill, Rank: 1
Column:        sex, Rank: 4
Column:     smoker, Rank: 1
Column:        day, Rank: 3
Column:       time, Rank: 2
Column:       size, Rank: 1
Column:   tip_rate, Rank: 1


In [27]:
data_rfe=pd.DataFrame(data,columns=X.columns)

In [28]:
data_rfe

total_bill  sex  smoker  day  time  size  tip_rate
0         16.99  0.0     0.0  3.0   1.0   2.0       6.0
1         10.34  1.0     0.0  3.0   1.0   3.0      16.0
2         21.01  1.0     0.0  3.0   1.0   3.0      17.0
3         23.68  1.0     0.0  3.0   1.0   2.0      14.0
4         24.59  0.0     0.0  3.0   1.0   4.0      15.0
..          ...  ...     ...  ...   ...   ...       ...
239       29.03  1.0     0.0  2.0   1.0   3.0      20.0
240       27.18  0.0     1.0  2.0   1.0   2.0       7.0
241       22.67  1.0     1.0  2.0   1.0   2.0       9.0
242       17.82  1.0     0.0  2.0   1.0   2.0      10.0
243       18.78  0.0     0.0  0.0   1.0   2.0      16.0

[244 rows x 7 columns]

In [29]:
data_rfe1=data_rfe.drop(['sex','day','time'],axis=1)

In [30]:
import pandas_profiling

In [31]:
data_rfe1.profile_report()

Summarize dataset:   0%|          | 0/17 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [32]:
data_rfe1.corr()

total_bill    smoker      size  tip_rate
total_bill    1.000000  0.085721  0.598315 -0.334753
smoker        0.085721  1.000000 -0.133178  0.029420
size          0.598315 -0.133178  1.000000 -0.141157
tip_rate     -0.334753  0.029420 -0.141157  1.000000

### PCA

In [33]:
from sklearn.decomposition import PCA

In [34]:
df_pca=df.values

In [35]:
df.describe()

total_bill         tip         sex      smoker         day        time  \
count  244.000000  244.000000  244.000000  244.000000  244.000000  244.000000   
mean    19.785943    2.998279    0.643443    0.381148    1.725410    0.721311   
std      8.902412    1.383638    0.479967    0.486667    1.155774    0.449276   
min      3.070000    1.000000    0.000000    0.000000    0.000000    0.000000   
25%     13.347500    2.000000    0.000000    0.000000    0.000000    0.000000   
50%     17.795000    2.900000    1.000000    0.000000    2.000000    1.000000   
75%     24.127500    3.562500    1.000000    1.000000    3.000000    1.000000   
max     50.810000   10.000000    1.000000    1.000000    3.000000    1.000000   

             size    tip_rate  
count  244.000000  244.000000  
mean     2.569672   16.094262  
std      0.951100    6.102968  
min      1.000000    4.000000  
25%      2.000000   13.000000  
50%      2.000000   15.500000  
75%      3.000000   19.000000  
max      6.000000   71.000000

In [36]:
trans = PCA(n_components=5)
data_dim = trans.fit_transform(df_pca)

In [37]:
trans.explained_variance_ratio_.cumsum()

array([0.71647432, 0.97658726, 0.98859636, 0.99362516, 0.99629452])

In [38]:
trans.components_

array([[-9.35315071e-01, -8.05179268e-02, -7.57778725e-03,
        -3.62456358e-03, -1.94695129e-02, -8.43648505e-03,
        -5.89584557e-02,  3.38682277e-01],
       [ 3.18406893e-01,  1.81348512e-01,  8.20290448e-04,
         6.31777870e-03,  2.38634172e-02,  5.75643538e-03,
         3.17231828e-02,  9.29559154e-01],
       [ 2.67224859e-02,  4.52836418e-02, -9.74387489e-02,
         2.29069567e-02, -9.36402057e-01, -3.26445544e-01,
        -6.08208339e-02,  1.00787650e-02],
       [-9.20908329e-02,  2.35222456e-01, -1.39673113e-02,
        -2.53025159e-01, -3.57062157e-02, -6.06984850e-02,
         9.30139304e-01, -4.30638244e-02],
       [ 1.01821175e-01, -8.81566545e-01, -7.62983703e-02,
         2.98743297e-01, -3.32429184e-02, -2.98117712e-02,
         3.15725812e-01,  1.25408352e-01]])

In [39]:
df_pca_trans=pd.DataFrame(data_dim)

In [40]:
df_pca_trans.describe().round(2)

0       1       2       3       4
count  244.00  244.00  244.00  244.00  244.00
mean     0.00   -0.00    0.00    0.00   -0.00
std      9.32    5.62    1.21    0.78    0.57
min    -29.00  -10.62   -1.67   -2.27   -2.25
25%     -4.83   -3.47   -1.02   -0.41   -0.26
50%      2.10   -0.62   -0.38   -0.13   -0.07
75%      6.13    2.65    1.48    0.34    0.20
max     30.15   47.45    2.51    3.12    3.64

In [41]:
df_pca_trans.profile_report()

Summarize dataset:   0%|          | 0/18 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

### Regression Feature Selection

In [42]:
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_regression

In [43]:
# define feature selection
fs = SelectKBest(score_func=f_regression, k=4)

In [44]:
X_selected = fs.fit_transform(data, y)

In [45]:
X_col=fs.get_support(indices=True)

In [46]:
X.columns

Index(['total_bill', 'sex', 'smoker', 'day', 'time', 'size', 'tip_rate'], dtype='object')

In [55]:
x_col=X.columns[X_col]

In [56]:
x_col

Index(['total_bill', 'day', 'size', 'tip_rate'], dtype='object')

In [57]:
x_reg_trans=pd.DataFrame(X_selected,columns=x_col)

In [59]:
X.profile_report()

Summarize dataset:   0%|          | 0/20 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [58]:
x_reg_trans.profile_report()

Summarize dataset:   0%|          | 0/17 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

### Standard scale

In [1]:
import pandas as pd

In [2]:
ori_data=pd.read_csv('tips.csv')

In [3]:
ori_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 244 entries, 0 to 243
Data columns (total 7 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   total_bill  244 non-null    float64
 1   tip         244 non-null    float64
 2   sex         244 non-null    object 
 3   smoker      244 non-null    object 
 4   day         244 non-null    object 
 5   time        244 non-null    object 
 6   size        244 non-null    int64  
dtypes: float64(2), int64(1), object(4)
memory usage: 13.5+ KB


### Encoding

In [4]:
ori_data.sex.replace({'Female':0,'Male':1},inplace=True)
ori_data.smoker.replace({'No':0,'Yes':1},inplace=True)
ori_data.day.replace({'Thur':0,'Fri':1,'Sat':2,'Sun':3},inplace=True)
ori_data.time.replace({'Lunch':0,'Dinner':1},inplace=True)

In [7]:
ori_data['tip_rate']=(ori_data.tip/ori_data.total_bill*100).round(2)

In [8]:
ori_data.describe()

total_bill         tip         sex      smoker         day        time  \
count  244.000000  244.000000  244.000000  244.000000  244.000000  244.000000   
mean    19.785943    2.998279    0.643443    0.381148    1.725410    0.721311   
std      8.902412    1.383638    0.479967    0.486667    1.155774    0.449276   
min      3.070000    1.000000    0.000000    0.000000    0.000000    0.000000   
25%     13.347500    2.000000    0.000000    0.000000    0.000000    0.000000   
50%     17.795000    2.900000    1.000000    0.000000    2.000000    1.000000   
75%     24.127500    3.562500    1.000000    1.000000    3.000000    1.000000   
max     50.810000   10.000000    1.000000    1.000000    3.000000    1.000000   

             size    tip_rate  
count  244.000000  244.000000  
mean     2.569672   16.079754  
std      0.951100    6.107020  
min      1.000000    3.560000  
25%      2.000000   12.910000  
50%      2.000000   15.475000  
75%      3.000000   19.147500  
max      6.000000   71.030000

### StandardScaler

In [9]:
from sklearn.preprocessing import StandardScaler

In [10]:
sc=StandardScaler()

In [11]:
ori_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 244 entries, 0 to 243
Data columns (total 8 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   total_bill  244 non-null    float64
 1   tip         244 non-null    float64
 2   sex         244 non-null    int64  
 3   smoker      244 non-null    int64  
 4   day         244 non-null    int64  
 5   time        244 non-null    int64  
 6   size        244 non-null    int64  
 7   tip_rate    244 non-null    float64
dtypes: float64(3), int64(5)
memory usage: 15.4 KB


In [12]:
sc_fit = sc.fit_transform(ori_data)

In [13]:
sc_data =pd.DataFrame(sc_fit,columns)

In [14]:
sc_data

0         1         2         3         4         5         6  \
0   -0.314711 -1.439947 -1.343353 -0.784789  1.105069  0.621582 -0.600193   
1   -1.063235 -0.969205  0.744406 -0.784789  1.105069  0.621582  0.453383   
2    0.137780  0.363356  0.744406 -0.784789  1.105069  0.621582  0.453383   
3    0.438315  0.225754  0.744406 -0.784789  1.105069  0.621582 -0.600193   
4    0.540745  0.443020 -1.343353 -0.784789  1.105069  0.621582  1.506958   
..        ...       ...       ...       ...       ...       ...       ...   
239  1.040511  2.115963  0.744406 -0.784789  0.238070  0.621582  0.453383   
240  0.832275 -0.722971 -1.343353  1.274228  0.238070  0.621582 -0.600193   
241  0.324630 -0.722971  0.744406  1.274228  0.238070  0.621582 -0.600193   
242 -0.221287 -0.904026  0.744406 -0.784789  0.238070  0.621582 -0.600193   
243 -0.113229  0.001247 -1.343353 -0.784789 -1.495930  0.621582 -0.600193   

            7  
0   -1.663757  
1   -0.004882  
2    0.095208  
3   -0.344533  
4   -0.229675  
..        ...  
239  0.707236  
240 -1.430760  
241 -1.191199  
242 -1.027117  
243 -0.018009  

[244 rows x 8 columns]